In [357]:
import pandas as pd
import altair as alt
import numpy as np

%config Completer.use_jedi = False

import datapane as dp

# Sign-in with your unique token
dp.login(token="b02ab14be52954a31156eb7242069f22d614c5d6")

Connected successfully to https://datapane.com as keith8


In [348]:
#uri = 'https://raw.githubusercontent.com/kejohns19/covid_analysis/main/covid_cdc_surveilance_summary.csv'
uri = 'https://raw.githubusercontent.com/kejohns19/covid_analysis/main/covid_cdc_surveilance_summary_3-24-21.csv'
df_surveil = pd.read_csv(uri)
df_surveil['date'] = pd.to_datetime({'year': df_surveil['Year'], 
                                     'month': df_surveil['Month'],
                                     'day': 1
                                    })
#df_surveil.date = pd.to_datetime(df_surveil.date)
df_surveil['Quarter'] = df_surveil['date'].dt.to_period('Q').astype('str')

In [349]:
df_surveil.head()

sex    age_group  Total_cases  Total_deaths  Month  Year Medcond  \
0  Female  0 - 9 Years            5             0      1  2020      No   
1  Female  0 - 9 Years           13             0      1  2020      No   
2  Female  0 - 9 Years           21             0      1  2020      No   
3  Female  0 - 9 Years            1             0      1  2020     Yes   
4  Female  0 - 9 Years            1             0      1  2020     Yes   

  Race_ethnicity       date Quarter  
0       Hispanic 2020-01-01  2020Q1  
1          White 2020-01-01  2020Q1  
2  Other/Missing 2020-01-01  2020Q1  
3          White 2020-01-01  2020Q1  
4          Black 2020-01-01  2020Q1

In [229]:
uri = 'https://raw.githubusercontent.com/kejohns19/covid_analysis/main/nc-est2019-asr6h.xlsx'
df_pop = pd.read_excel(uri, sheet_name='Summary')

# add summary fields for Age and sex
totals = df_pop.groupby('Age Range').sum()
totals['sex'] = 'Both'
df_pop = df_pop.append(totals.reset_index())
totals = df_pop.groupby(['sex']).sum()
totals['Age Range'] = 'All'
df_pop = df_pop.append(totals.reset_index())
df_pop.head()

Age Range   sex     Total     White    Black    Asian    AIAN   NHPI  \
0    0 - 9 Years  Male  20331969  10111533  2767293  1016528  170680  40935   
1  10 - 19 Years  Male  21363868  11024966  2913005  1089176  179761  42616   
2  20 - 29 Years  Male  23069322  12418470  3310805  1416195  194625  48197   
3  30 - 39 Years  Male  22239551  12498632  2816469  1560045  167308  52038   
4  40 - 49 Years  Male  19992494  11771175  2396453  1330944  140078  39608   

   2 or more  Hispanic  
0     955733   5269267  
1     829934   5284410  
2     630853   5050177  
3     389297   4755762  
4     274284   4039952

In [230]:
uri = 'https://raw.githubusercontent.com/kejohns19/covid_analysis/main/nc-est2019-asr6h.xlsx'
df_pop = pd.read_excel(uri, sheet_name='Summary')

# add summary fields for Age and sex
totals = df_pop.groupby('Age Range').sum()
totals['sex'] = 'Both'
df_pop = df_pop.append(totals.reset_index())
totals = df_pop.groupby(['sex']).sum()
totals['Age Range'] = 'All'
df_pop = df_pop.append(totals.reset_index())

df_pop_percent = df_pop[['Age Range', 'sex', 'White', 'Black', 'Asian', 'Hispanic']]
df_pop_percent['Total'] = df_pop_percent.sum(1)
df_pop_percent[['White', 'Black', 'Asian', 'Hispanic']] = df_pop_percent[['White', 'Black', 'Asian', 'Hispanic']].div(df_pop_percent['Total'], axis=0) * 100

/home/johnsonke6/anaconda3/envs/analysis/lib/python3.7/site-packages/ipykernel_launcher.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  del sys.path[0]
/home/johnsonke6/anaconda3/envs/analysis/lib/python3.7/site-packages/pandas/core/frame.py:3191: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[k1] = value[k2]


In [25]:
age_ranges = ['0 - 9 Years',
 '10 - 19 Years',
 '20 - 29 Years',
 '30 - 39 Years',
 '40 - 49 Years',
 '50 - 59 Years',
 '60 - 69 Years',
 '70 - 79 Years',
 '80+ Years']

In [215]:
data = df_surveil[df_surveil['age_group'].isin(age_ranges)]
data = data[data['sex'].isin(['Female', 'Male'])]

input_dropdown = alt.binding_radio(options=data['Race_ethnicity'].unique(), name='Race/Ethnicity')
selection = alt.selection_single(fields=['Race_ethnicity'], bind=input_dropdown)

input_dropdown2 = alt.binding_radio(options=data['Quarter'].unique())
selection2 = alt.selection_single(fields=['Quarter'], bind=input_dropdown, name='')

plot = alt.Chart(data).mark_bar()
plot = plot.encode(
    x=alt.X('age_group', title='Age group', axis=alt.Axis(labelAngle=-65)),
    y=alt.Y('sum(Total_cases)',title='Total cases'),
    color=alt.Color('age_group'),
    #column=alt.Column('Quarter', title='Total Cases By Quarter and Age Group'),
    #row=alt.Row('sex')
).properties(
    width=250
).add_selection(
    selection
).transform_filter(
    selection
)
'''.add_selection(
    selection2
).transform_filter(
    selection2
)'''

plot

alt.Chart(...)

In [252]:
list(data['Race_ethnicity'].unique()) + [None]

['Hispanic', 'White', 'Black', 'Other/Missing', 'Asian', None]

In [50]:
input_dropdown = alt.binding_radio(options=[None] + age_ranges, 
                                   labels=['All '] + [x[:-5] for x in age_ranges], 
                                   name='Age Range in Years: ')
selection = alt.selection_single(fields=['age_group'], bind=input_dropdown)

input_dropdown2 = alt.binding_radio(options=[None, 'Female', 'Male'], 
                                    labels=['Both ', 'Female ', 'Male '], name='Sex: ')
selection2 = alt.selection_single(fields=['sex'], bind=input_dropdown2)

#data = df_surveil[df_surveil['sex'].isin(['Female', 'Male'])]
data = data[~data['Race_ethnicity'].isin(['Other/Missing'])]

base = alt.Chart(data)
base = base.add_selection(
    selection
).transform_filter(
    selection
).add_selection(
    selection2
).transform_filter(
    selection2
).transform_aggregate(
    sum_deaths='sum(Total_deaths)',
    sum_cases='sum(Total_cases)',
    groupby=['Race_ethnicity', 'Quarter']
)

base = base.transform_calculate(
    Percent_deaths="100 * datum.sum_deaths / datum.sum_cases")
base = base.mark_bar(size=35)
base = base.encode(
    x=alt.X('Race_ethnicity', title='Race/Ethnicity', axis=alt.Axis(labelAngle=-65)),
    y=alt.Y('Percent_deaths:Q', 
            title='% deaths of all cases',
            scale=alt.Scale(domain=(0, 20))
           ),
    color=alt.Color('Race_ethnicity', legend=None),
    column=alt.Column('Quarter', title='% Deaths By Quarter and Age Group')
).properties(
    width=160
)


base

alt.Chart(...)

In [350]:
data = df_surveil[df_surveil['age_group'].isin(age_ranges)]
base = alt.Chart(data)
base = base.transform_aggregate(
    sum_deaths='sum(Total_deaths)',
    sum_cases='sum(Total_cases)',
    groupby=['age_group', 'Quarter']
)
base = base.transform_calculate(
    Percent_deaths="100 * datum.sum_deaths / datum.sum_cases")
base = base.mark_bar()
base = base.encode(
    x=alt.X('age_group', title='Age group', axis=alt.Axis(labelAngle=-65)),
    y=alt.Y('Percent_deaths:Q',title='% deaths of all cases'),
    color=alt.Color('age_group', legend=None),
    #column=alt.Column('Quarter', title='% Deaths By Quarter and Age Group')
)

plot = alt.layer(
  base,
  base.mark_text(dy=-5, size=8).encode(text=alt.Text('Percent_deaths:Q', format=',.1f'))
).facet(
    column=alt.Column('Quarter', title='% Deaths By Quarter and Age Group'),
    row=alt.Row('Medcond', title='Has Pre-existing Medical Condition?')
)

plot

alt.FacetChart(...)

In [351]:
input_dropdown = alt.binding_radio(options=[None] + age_ranges, 
                                   labels=['All '] + [x[:-5] for x in age_ranges], 
                                   name='Age Range in Years: ')
selection = alt.selection_single(fields=['age_group'], bind=input_dropdown)

input_dropdown2 = alt.binding_radio(options=[None, 'Female', 'Male'], 
                                    labels=['Both ', 'Female ', 'Male '], name='Sex: ')
selection2 = alt.selection_single(fields=['sex'], bind=input_dropdown2)

data = df_surveil[df_surveil['sex'].isin(['Female', 'Male'])]
data = data[~data['Race_ethnicity'].isin(['Other/Missing'])]

base = alt.Chart(data)
base = base.transform_aggregate(
    sum_deaths='sum(Total_deaths)',
    sum_cases='sum(Total_cases)',
    groupby=['Race_ethnicity', 'Quarter']
)
base = base.transform_calculate(
    Percent_deaths="100 * datum.sum_deaths / datum.sum_cases")
base = base.mark_bar(size=35)
base = base.encode(
    x=alt.X('Race_ethnicity', title='Race/Ethnicity', axis=alt.Axis(labelAngle=-65)),
    y=alt.Y('Percent_deaths:Q',title='% deaths of all cases'),
    color=alt.Color('Race_ethnicity', legend=None),
    #column=alt.Column('Quarter', title='% Deaths By Quarter and Age Group')
).properties(width=155)

plot = alt.layer(
  base,
  base.mark_text(dy=-7, size=10, fontStyle='bold').encode(text=alt.Text('Percent_deaths:Q', format=',.1f'))
).facet(
    column=alt.Column('Quarter', header=alt.Header(titleFontSize=14), title='% Deaths By Quarter and Race/Ethnicity'),
    row=alt.Row('sex', header=alt.Header(titleFontSize=14), title='Sex')
)

plot

alt.FacetChart(...)

In [352]:
# reformat data to combine younger age groups
data = df_surveil[df_surveil['age_group'].isin(age_ranges)]
age_less_than_30 = ['0 - 9 Years', '10 - 19 Years', '20 - 29 Years', '30 - 39 Years']
mask = data['age_group'].isin(age_less_than_30)
data['age_group'] = np.where(mask, '39 or less Years', data['age_group'])

race_types = list(data['Race_ethnicity'].unique())
input_dropdown = alt.binding_radio(options=[None] + race_types, 
                  labels=['All'] + race_types,
                  name='Race/Ethnicity :')
selection = alt.selection_single(fields=['Race_ethnicity'], bind=input_dropdown)

data = data[data['sex'].isin(['Female', 'Male'])]
base = alt.Chart(data)
base = base.transform_aggregate(
    sum_deaths='sum(Total_deaths)',
    sum_cases='sum(Total_cases)',
    groupby=['age_group', 'Quarter']
)
base = base.transform_calculate(
    Percent_deaths="100 * datum.sum_deaths / datum.sum_cases")
base = base.mark_bar()
base = base.encode(
    x=alt.X('age_group', title='Age group', axis=alt.Axis(labelAngle=-65)),
    y=alt.Y('Percent_deaths:Q',title='% deaths of all cases', scale=alt.Scale(domain=(0, 65))),
    color=alt.Color('age_group', legend=None),
    #column=alt.Column('Quarter', title='% Deaths By Quarter and Age Group')
)

plot1 = alt.layer(
  base,
  base.mark_text(
      dy=-7, size=10, fontStyle='bold', color='black'
  )
).properties(
    width=155
).encode(
    text=alt.Text('Percent_deaths:Q', format=',.1f')
).facet(
    column=alt.Column('Quarter', header=alt.Header(titleFontSize=18), title='% Deaths By Quarter and Race/Ethnicity'),
    row=alt.Row('sex', header=alt.Header(titleFontSize=16), title='Sex'),
).add_selection(
    selection
).transform_filter(
    selection
)

plot1

/home/johnsonke6/anaconda3/envs/analysis/lib/python3.7/site-packages/ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """


alt.FacetChart(...)

In [355]:
input_dropdown = alt.binding_radio(options=[None] + age_ranges, 
                                   labels=['All '] + [x[:-5] for x in age_ranges], 
                                   name='Age Range in Years: ')
selection = alt.selection_single(fields=['age_group'], bind=input_dropdown)

input_dropdown2 = alt.binding_radio(options=[None, 'Female', 'Male'], 
                                    labels=['Both ', 'Female ', 'Male '], name='Sex: ')
selection2 = alt.selection_single(fields=['sex'], bind=input_dropdown2)


data = df_surveil[~df_surveil['Race_ethnicity'].isin(['Other/Missing'])]
base = alt.Chart(data)
base = base.transform_aggregate(
    sum_deaths='sum(Total_deaths)',
    sum_cases='sum(Total_cases)',
    groupby=['Race_ethnicity', 'Quarter']
)

base = base.transform_calculate(
    Percent_deaths="100 * datum.sum_deaths / datum.sum_cases")
base = base.mark_bar()
base = base.encode(
    x=alt.X('Race_ethnicity', title='Race/Ethnicity', axis=alt.Axis(labelAngle=-65)),
    y=alt.Y('Percent_deaths:Q', 
            title='% deaths of all cases',
            scale=alt.Scale(domain=(0, 70))
           ),
    color=alt.Color('Race_ethnicity', legend=None),
    #column=alt.Column('Quarter', title='% Deaths By Quarter and Age Group')
).properties(width=155)

plot2 = alt.layer(
  base,
  base.mark_text(dy=-7, size=10, fontStyle='bold').encode(text=alt.Text('Percent_deaths:Q', format=',.1f'))
).facet(
    column=alt.Column('Quarter', header=alt.Header(titleFontSize=18), title='% Deaths By Quarter and Race/Ethnicity'),
    row=alt.Row('Medcond', header=alt.Header(titleFontSize=16), title='Has Pre-existing Medical Condition?')
).add_selection(
    selection
).transform_filter(
    selection
).add_selection(
    selection2
).transform_filter(
    selection2
)

plot2

alt.FacetChart(...)

In [358]:
# Create report
r = dp.Report(
    f'### Comparing Percentage of Confirmed COVID-19 Cases that end in Death by Quarter for Age Groups an Race/Ethnicities',
    f'_Built using data from [CDC COVID-19 Case Surveillance Data](https://data.cdc.gov/Case-Surveillance/COVID-19-Case-Surveillance-Public-Use-Data/vbim-akqf) on 3/1/2021_',
    f'The first chart highlights the percentage of deaths to confirmed cases over each quarter, starting with Q1 2020, for various age groups.  For convinience all age under 40 Years are combined since the percentages are so small.  The top sublot is for females and the bottom subplot is for males. Noticeably the percentage of deaths drops each quarter for each age group.  The radio buttons on the bottom can be used to select and explore a specific race/ethnicity.',
    f'There are likley several explanatory reasons for the positive trend towards less deaths as a percentage of confirmed cases, including: better treatment options, earlier detection, greater proliferation of testing, etc.',
    f'Also of note males consistently have a higher deaths as a percentage of confirmed cases than females across all quarters and across all race/ethnicities. ',
    dp.Plot(plot1),
    f'The next chart breaks out the percentage of confirmed cases that result in death over each quarter for each race/ethnicity.  The top subplot includes those individuals who do not have a prior medical condition while the bottom only incluldes those who had a prior medical condition.  The radio buttons on the bottom allows specification of sex as well as selection and exploration of a specific age group.  Unlike the prior chart, the younger age groups are not combined.',
    f'Examining the last few quarters, people categorized as Asian and Black appear to have the higher deaths as a percentage of confirmed cases as compared to people categorized as Hispanic or White.',
    dp.Plot(plot2),
)

# Publish
r.publish(name=f'COVID-19 Trends by Quarter', open=True, description=f'COVID-19 Trends by Quarter')
                    

Publishing report and associated data - please wait..
Report successfully published at https://datapane.com/u/keith8/reports/covid-19-trends-by-quarter/


In [213]:
ages = ['50 - 59 Years', '60 - 69 Years', '70 - 79 Years', '80+ Years']
df_temp = df_pop_percent[(df_pop_percent['Age Range'].isin(ages)) & (df_pop_percent['sex'] == sex)]
df_temp.melt(id_vars=['Age Range', 'sex'], var_name='Race_ethnicity', value_name='Race_Percent')


Age Range   sex Race_ethnicity  Race_Percent
0   50 - 59 Years  Male          White  6.780481e+01
1   60 - 69 Years  Male          White  7.462737e+01
2   70 - 79 Years  Male          White  7.930725e+01
3       80+ Years  Male          White  8.027339e+01
4   50 - 59 Years  Male          Black  1.178612e+01
5   60 - 69 Years  Male          Black  1.041437e+01
6   70 - 79 Years  Male          Black  8.184692e+00
7       80+ Years  Male          Black  7.089651e+00
8   50 - 59 Years  Male          Asian  5.271585e+00
9   60 - 69 Years  Male          Asian  4.635896e+00
10  70 - 79 Years  Male          Asian  4.414507e+00
11      80+ Years  Male          Asian  4.628264e+00
12  50 - 59 Years  Male       Hispanic  1.513749e+01
13  60 - 69 Years  Male       Hispanic  1.032237e+01
14  70 - 79 Years  Male       Hispanic  8.093550e+00
15      80+ Years  Male       Hispanic  8.008690e+00
16  50 - 59 Years  Male          Total  2.032717e+07
17  60 - 69 Years  Male          Total  1.774600e+07
18  70 - 79 Years  Male          Total  1.066019e+07
19      80+ Years  Male          Total  4.992714e+06

In [206]:
ages = ['50 - 59 Years', '60 - 69 Years', '70 - 79 Years', '80+ Years']
ages = ['50 - 59 Years']
age = '50+ Years'
sex = 'Both'
sex = 'Male'
df_temp = df_pop_percent[(df_pop_percent['Age Range'] == age) & (df_pop_percent['sex'] == sex)]
df_temp = df_temp.melt(id_vars=['Age Range', 'sex'], var_name='Race_ethnicity', value_name='Race_Percent')

df = df_surveil[~df_surveil['Race_ethnicity'].isin(['Other/Missing'])]
df = df[df['sex'] == sex]
df = df[df['age_group'].isin(ages)]

df = df.groupby(['Quarter', 'Medcond', 'Race_ethnicity'])['Total_cases', 'Total_deaths'].sum()

df[['%cases', '%deaths']] = (df / df.sum(level=[0,1]).reindex(df.index) * 100)
df = df.reset_index().merge(df_temp, on='Race_ethnicity', how='left')

/home/johnsonke6/anaconda3/envs/analysis/lib/python3.7/site-packages/ipykernel_launcher.py:13: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  del sys.path[0]


In [337]:
base = alt.Chart(df)
title = '% Deaths By Quarter and Race/Ethnicity for Sex = {} and Age= {}'.format(sex, age)

plot1 = base.mark_bar(size=35)
plot1 = plot1.encode(
    x=alt.X('Race_ethnicity', title='Race/Ethnicity', axis=alt.Axis(labelAngle=-65)),
    y=alt.Y('%deaths:Q',title='% deaths by race/ethnicity'),
    color=alt.Color('Race_ethnicity', legend=None),
).properties(width=155)

plot_deaths = alt.layer(
  plot1,
  plot1.mark_text(dy=-5, size=10).encode(text=alt.Text('%deaths:Q', format=',.1f')),
  base.mark_tick(color='red', thickness=3).encode(x='Race_ethnicity', y='Race_Percent:Q'),
).facet(
    column=alt.Column('Quarter', header=alt.Header(titleFontSize=14), title=title),
    #row=alt.Row('Medcond', header=alt.Header(titleFontSize=14), title='Has Pre-existing Medical Condition?'),
    #title=title
)

base = alt.Chart(df)
title = '% Cases By Quarter and Race/Ethnicity for Sex = {} and Age= {}'.format(sex, age)

plot1 = base.mark_bar(size=35)
plot1 = plot1.encode(
    x=alt.X('Race_ethnicity', title='Race/Ethnicity', axis=alt.Axis(labelAngle=-65)),
    y=alt.Y('%cases:Q',title='% cases by race/ethnicity'),
    color=alt.Color('Race_ethnicity', legend=None),
).properties(width=155)

plot_cases = alt.layer(
  plot1,
  plot1.mark_text(dy=-5, size=10).encode(text=alt.Text('%cases:Q', format=',.1f')),
  base.mark_tick(color='red', thickness=3).encode(x='Race_ethnicity', y='Race_Percent:Q'),
).facet(
    column=alt.Column('Quarter', header=alt.Header(titleFontSize=14), title=title),
    #row=alt.Row('Medcond', header=alt.Header(titleFontSize=14), title='Has Pre-existing Medical Condition?'),
    #title=title
)

In [338]:
alt.vconcat(plot_cases, plot_deaths)

alt.VConcatChart(...)

In [177]:
df_temp = df_pop_percent.melt(id_vars=['Age Range', 'sex'], var_name='Race_ethnicity', value_name='Race_Percent')

df = df_surveil[~df_surveil['Race_ethnicity'].isin(['Other/Missing'])]
df = df.groupby(['Quarter', 'Medcond', 'Race_ethnicity', 'age_group', 'sex'])['Total_cases', 'Total_deaths'].sum()

df[['%cases', '%deaths']] = (df / df.sum(level=[0,1]).reindex(df.index) * 100)
df = df.reset_index()
df['Age Range'] = df['age_group']
del df['age_group']
#df = df.merge(df_temp, on=['Race_ethnicity', 'sex', 'Age Range'], how='left')

/home/johnsonke6/anaconda3/envs/analysis/lib/python3.7/site-packages/ipykernel_launcher.py:4: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  after removing the cwd from sys.path.


In [194]:
df

Quarter Medcond Race_ethnicity  Total_cases  Total_deaths     %cases  \
0   2020Q1      No          Asian         1294            44   4.892250   
1   2020Q1      No          Black         5702           241  21.557656   
2   2020Q1      No       Hispanic         6449           232  24.381853   
3   2020Q1      No          White        13005           236  49.168242   
4   2020Q1     Yes          Asian          623            91   4.940132   
5   2020Q1     Yes          Black         3672           551  29.117437   
6   2020Q1     Yes       Hispanic         3395           536  26.920942   
7   2020Q1     Yes          White         4921           391  39.021489   
8   2020Q2      No          Asian         5682           121   4.140494   
9   2020Q2      No          Black        29008           759  21.138235   
10  2020Q2      No       Hispanic        49300           962  35.925089   
11  2020Q2      No          White        53240           887  38.796182   
12  2020Q2     Yes          Asian         1692           118   4.248268   
13  2020Q2     Yes          Black         9941           702  24.959827   
14  2020Q2     Yes       Hispanic        12674           733  31.821834   
15  2020Q2     Yes          White        15521           720  38.970071   
16  2020Q3      No          Asian         6163            80   2.797650   
17  2020Q3      No          Black        37940           694  17.222595   
18  2020Q3      No       Hispanic        51384           658  23.325404   
19  2020Q3      No          White       124805          1007  56.654350   
20  2020Q3     Yes          Asian          840            24   2.472042   
21  2020Q3     Yes          Black         6335           149  18.643320   
22  2020Q3     Yes       Hispanic         5694           128  16.756916   
23  2020Q3     Yes          White        21111           265  62.127722   
24  2020Q4      No          Asian        25277           244   3.680895   
25  2020Q4      No          Black        67932           912   9.892414   
26  2020Q4      No       Hispanic       103958          1036  15.138603   
27  2020Q4      No          White       489541          2818  71.288088   
28  2020Q4     Yes          Asian         2033            31   3.110322   
29  2020Q4     Yes          Black         8684           206  13.285804   
30  2020Q4     Yes       Hispanic         9266           165  14.176216   
31  2020Q4     Yes          White        45380           454  69.427658   
32  2021Q1      No          Asian        16112            79   5.416709   
33  2021Q1      No          Black        39372           316  13.236510   
34  2021Q1      No       Hispanic        43261           279  14.543957   
35  2021Q1      No          White       198705           860  66.802824   
36  2021Q1     Yes          Asian         1594            19   5.815184   
37  2021Q1     Yes          Black         5012            94  18.284630   
38  2021Q1     Yes       Hispanic         6365            76  23.220605   
39  2021Q1     Yes          White        14440           115  52.679581   

      %deaths      Age Range   sex  Race_Percent  
0    5.843293  50 - 59 Years  Both      5.584778  
1   32.005312  50 - 59 Years  Both     12.407433  
2   30.810093  50 - 59 Years  Both     14.842324  
3   31.341301  50 - 59 Years  Both     67.165464  
4    5.799873  50 - 59 Years  Both      5.584778  
5   35.117909  50 - 59 Years  Both     12.407433  
6   34.161887  50 - 59 Years  Both     14.842324  
7   24.920331  50 - 59 Years  Both     67.165464  
8    4.433859  50 - 59 Years  Both      5.584778  
9   27.812385  50 - 59 Years  Both     12.407433  
10  35.251008  50 - 59 Years  Both     14.842324  
11  32.502748  50 - 59 Years  Both     67.165464  
12   5.191377  50 - 59 Years  Both      5.584778  
13  30.884294  50 - 59 Years  Both     12.407433  
14  32.248130  50 - 59 Years  Both     14.842324  
15  31.676199  50 - 59 Years  Both     67.165464  
16   3.280033  50 - 59 Years  Both      5.584778  
17  28.45

In [178]:
df

Quarter Medcond Race_ethnicity      sex  Total_cases  Total_deaths  \
0     2020Q1      No          Asian   Female           25             0   
1     2020Q1      No          Asian     Male           33             0   
2     2020Q1      No          Asian   Female           65             0   
3     2020Q1      No          Asian     Male           53             0   
4     2020Q1      No          Asian  Unknown            2             0   
...      ...     ...            ...      ...          ...           ...   
1496  2021Q1     Yes          White  Missing            1             0   
1497  2021Q1     Yes          White  Unknown            8             2   
1498  2021Q1     Yes          White   Female            5             0   
1499  2021Q1     Yes          White     Male            3             0   
1500  2021Q1     Yes          White  Missing            1             0   

        %cases   %deaths      Age Range  
0     0.017938  0.000000    0 - 9 Years  
1     0.023678  0.000000    0 - 9 Years  
2     0.046638  0.000000  10 - 19 Years  
3     0.038028  0.000000  10 - 19 Years  
4     0.001435  0.000000  10 - 19 Years  
...        ...       ...            ...  
1496  0.000673  0.000000      80+ Years  
1497  0.005382  0.043869      80+ Years  
1498  0.003364  0.000000        Missing  
1499  0.002018  0.000000        Missing  
1500  0.000673  0.000000        Missing  

[1501 rows x 9 columns]

In [179]:
df_temp

Age Range     sex Race_ethnicity  Race_Percent
0      0 - 9 Years    Male          White  5.276146e+01
1    10 - 19 Years    Male          White  5.427928e+01
2    20 - 29 Years    Male          White  5.595002e+01
3    30 - 39 Years    Male          White  5.778136e+01
4    40 - 49 Years    Male          White  6.024598e+01
..             ...     ...            ...           ...
145  70 - 79 Years    Both          Total  2.333624e+07
146      80+ Years    Both          Total  1.276418e+07
147            All    Both          Total  3.179354e+08
148            All  Female          Total  1.613681e+08
149            All    Male          Total  1.565673e+08

[150 rows x 4 columns]

In [174]:
df

Quarter Medcond Race_ethnicity      sex  Total_cases  Total_deaths  \
0     2020Q1      No          Asian   Female           25             0   
1     2020Q1      No          Asian     Male           33             0   
2     2020Q1      No          Asian   Female           65             0   
3     2020Q1      No          Asian     Male           53             0   
4     2020Q1      No          Asian  Unknown            2             0   
...      ...     ...            ...      ...          ...           ...   
1496  2021Q1     Yes          White  Missing            1             0   
1497  2021Q1     Yes          White  Unknown            8             2   
1498  2021Q1     Yes          White   Female            5             0   
1499  2021Q1     Yes          White     Male            3             0   
1500  2021Q1     Yes          White  Missing            1             0   

        %cases   %deaths      Age Range  Race_Percent  
0     0.017938  0.000000    0 - 9 Years      5.254501  
1     0.023678  0.000000    0 - 9 Years      5.304190  
2     0.046638  0.000000  10 - 19 Years      5.515496  
3     0.038028  0.000000  10 - 19 Years      5.362346  
4     0.001435  0.000000  10 - 19 Years           NaN  
...        ...       ...            ...           ...  
1496  0.000673  0.000000      80+ Years           NaN  
1497  0.005382  0.043869      80+ Years           NaN  
1498  0.003364  0.000000        Missing           NaN  
1499  0.002018  0.000000        Missing           NaN  
1500  0.000673  0.000000        Missing           NaN  

[1501 rows x 10 columns]

In [168]:
df[(df['Quarter'] == '2020Q1') & (df['Medcond'] == 'No')]

Quarter Medcond Race_ethnicity    age_group    sex_x  Total_cases  \
0     2020Q1      No          Asian  0 - 9 Years   Female           25   
1     2020Q1      No          Asian  0 - 9 Years   Female           25   
2     2020Q1      No          Asian  0 - 9 Years   Female           25   
3     2020Q1      No          Asian  0 - 9 Years   Female           25   
4     2020Q1      No          Asian  0 - 9 Years   Female           25   
...      ...     ...            ...          ...      ...          ...   
4105  2020Q1      No          White      Missing  Unknown            1   
4106  2020Q1      No          White      Missing  Unknown            1   
4107  2020Q1      No          White      Missing  Unknown            1   
4108  2020Q1      No          White      Missing  Unknown            1   
4109  2020Q1      No          White      Missing  Unknown            1   

      Total_deaths    %cases  %deaths      Age Range   sex_y  Race_Percent  
0                0  0.017938      0.0    0 - 9 Years    Male      5.304190  
1                0  0.017938      0.0  10 - 19 Years    Male      5.362346  
2                0  0.017938      0.0  20 - 29 Years    Male      6.380508  
3                0  0.017938      0.0  30 - 39 Years    Male      7.212111  
4                0  0.017938      0.0  40 - 49 Years    Male      6.811896  
...            ...       ...      ...            ...     ...           ...  
4105             0  0.000718      0.0  70 - 79 Years    Both     77.931887  
4106             0  0.000718      0.0      80+ Years    Both     79.181201  
4107             0  0.000718      0.0            All    Both     62.059716  
4108             0  0.000718      0.0            All  Female     61.968104  
4109             0  0.000718      0.0            All    Male     62.154137  

[4110 rows x 12 columns]

In [151]:
input_dropdown = alt.binding_radio(options=['All'] + age_ranges, 
                                   labels=['All '] + [x[:-5] for x in age_ranges], 
                                   name='Age Range in Years: ')
selection = alt.selection_single(fields=['Age Range'], bind=input_dropdown, init={'Age Range': 'All'})

input_dropdown2 = alt.binding_radio(options=['Both', 'Female', 'Male'], 
                                    labels=['Both ', 'Female ', 'Male '], name='Sex: ')
selection2 = alt.selection_single(fields=['sex'], bind=input_dropdown2)

base = alt.Chart(df)
title = '% Deaths By Quarter and Race/Ethnicity'

'''base = base.add_selection(
    selection
).transform_filter(
    selection
)'''

plot1 = base.mark_bar(size=35)
plot1 = plot1.encode(
    x=alt.X('Race_ethnicity', title='Race/Ethnicity', axis=alt.Axis(labelAngle=-65)),
    y=alt.Y('mean(%deaths):Q',title='% deaths by race/ethnicity'),
    color=alt.Color('Race_ethnicity', legend=None),
).properties(width=155)

plot_deaths = alt.layer(
  plot1,
  plot1.mark_text(dy=-9, size=12).encode(text=alt.Text('%deaths:Q', format=',.1f')),
  #base.mark_tick(color='red', thickness=3).encode(x='Race_ethnicity', y='Race_Percent:Q'),
).facet(
    column=alt.Column('Quarter', header=alt.Header(titleFontSize=14), title=title),
    row=alt.Row('Medcond', header=alt.Header(titleFontSize=14), title='Has Pre-existing Medical Condition?'),
)

plot_deaths

alt.FacetChart(...)